<a href="https://colab.research.google.com/github/Rgalitzdorfer/Algorithmic-Trading/blob/main/Momentum_Algorithmic_Trading.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

**Table of Contents**

1.   Data Collection
2.   Hypothesis
3.   Strategy Creation
4.   Backtesting





1. **Data Collection**

In [ ]:
#Install TA-Lib & vectorbt
!wget http://prdownloads.sourceforge.net/ta-lib/ta-lib-0.4.0-src.tar.gz
!tar -xzvf ta-lib-0.4.0-src.tar.gz
%cd ta-lib
!./configure --prefix=/usr
!make
!make install
!pip install TA-Lib
!pip install vectorbt

In [26]:
#Import useful libraries
import pandas as pd #Data processing
import numpy as np #Linear Algebra
import vectorbt as vbt #Backtesting
import talib as ta #Technical Analysis
import yfinance as yf #Historical Market Data

In [27]:
#Read dataset
data = yf.download('BTC-USD', start = '2022-02-01', end = '2024-01-01', interval = '1h')
data.head()

[*********************100%%**********************]  1 of 1 completed


Open          High           Low  \
Datetime                                                              
2022-02-01 00:00:00+00:00  38481.765625  38545.562500  38336.601562   
2022-02-01 01:00:00+00:00  38340.218750  38392.253906  38223.531250   
2022-02-01 02:00:00+00:00  38266.632812  38489.617188  38256.949219   
2022-02-01 03:00:00+00:00  38472.097656  38622.914062  38430.562500   
2022-02-01 04:00:00+00:00  38617.210938  38639.039062  38532.636719   

                                  Close     Adj Close     Volume  
Datetime                                                          
2022-02-01 00:00:00+00:00  38341.386719  38341.386719          0  
2022-02-01 01:00:00+00:00  38265.773438  38265.773438          0  
2022-02-01 02:00:00+00:00  38468.675781  38468.675781          0  
2022-02-01 03:00:00+00:00  38615.339844  38615.339844  268036096  
2022-02-01 04:00:00+00:00  38575.039062  38575.039062   33286144

In [28]:
#Check for null values
data.isnull().sum()

Open         0
High         0
Low          0
Close        0
Adj Close    0
Volume       0
dtype: int64

2. **Hypothesis**

This strategy aims to capitalize on momentum in a volatile trending market by combining ADX to measure trend strength, the RSI for entry signals, the 50 EMA to determine trend direction, and a candlestick close outside of the previous range. A return of the ADX to nornal conditions signifies a decrease in momentum and is used to exit the trade. All backtesting will be performed in the last 2 years on a volatile currency pair such as Bitcoin.








3. **Strategy Creation**

In [29]:
#Create Columns for Indicators
#ADX for Trend Strength
data['ADX'] = ta.ADX(data.High, data.Low, data.Close, timeperiod = 14)

#RSI for Entry Trigger
data['RSI'] = ta.RSI(data.Close, timeperiod = 14)

#50 EMA for Trend Direction
data['50_EMA'] = ta.EMA(data['Close'], timeperiod = 50)

data.head()

Open          High           Low  \
Datetime                                                              
2022-02-01 00:00:00+00:00  38481.765625  38545.562500  38336.601562   
2022-02-01 01:00:00+00:00  38340.218750  38392.253906  38223.531250   
2022-02-01 02:00:00+00:00  38266.632812  38489.617188  38256.949219   
2022-02-01 03:00:00+00:00  38472.097656  38622.914062  38430.562500   
2022-02-01 04:00:00+00:00  38617.210938  38639.039062  38532.636719   

                                  Close     Adj Close     Volume  ADX  RSI  \
Datetime                                                                     
2022-02-01 00:00:00+00:00  38341.386719  38341.386719          0  NaN  NaN   
2022-02-01 01:00:00+00:00  38265.773438  38265.773438          0  NaN  NaN   
2022-02-01 02:00:00+00:00  38468.675781  38468.675781          0  NaN  NaN   
2022-02-01 03:00:00+00:00  38615.339844  38615.339844  268036096  NaN  NaN   
2022-02-01 04:00:00+00:00  38575.039062  38575.039062   33286144  NaN  NaN   

                           50_EMA  
Datetime                           
2022-02-01 00:00:00+00:00     NaN  
2022-02-01 01:00:00+00:00     NaN  
2022-02-01 02:00:00+00:00     NaN  
2022-02-01 03:00:00+00:00     NaN  
2022-02-01 04:00:00+00:00     NaN

In [30]:
#Create new column for identifying trend
data['Trend_Direction'] = 0

#Uptrend (Minimum of 10 closes)
data.loc[data['Close'] > data['50_EMA'], 'Trend_Direction'] = 1
data['Uptrend_Continuation'] = data['Trend_Direction'].rolling(window=10).sum() == 10

#Downtrend (Minimum of 10 closes)
data.loc[data['Close'] < data['50_EMA'], 'Trend_Direction'] = -1
data['Downtrend_Continuation'] = data['Trend_Direction'].rolling(window=10).sum() == -10

#More confirmation on potential trend breakout
data['Buy_Signal'] = data['Close'] > data['Close'].shift(1).rolling(window=25).max()
data['Sell_Signal'] = data['Close'] < data['Close'].shift(1).rolling(window=25).min()

data.head()

Open          High           Low  \
Datetime                                                              
2022-02-01 00:00:00+00:00  38481.765625  38545.562500  38336.601562   
2022-02-01 01:00:00+00:00  38340.218750  38392.253906  38223.531250   
2022-02-01 02:00:00+00:00  38266.632812  38489.617188  38256.949219   
2022-02-01 03:00:00+00:00  38472.097656  38622.914062  38430.562500   
2022-02-01 04:00:00+00:00  38617.210938  38639.039062  38532.636719   

                                  Close     Adj Close     Volume  ADX  RSI  \
Datetime                                                                     
2022-02-01 00:00:00+00:00  38341.386719  38341.386719          0  NaN  NaN   
2022-02-01 01:00:00+00:00  38265.773438  38265.773438          0  NaN  NaN   
2022-02-01 02:00:00+00:00  38468.675781  38468.675781          0  NaN  NaN   
2022-02-01 03:00:00+00:00  38615.339844  38615.339844  268036096  NaN  NaN   
2022-02-01 04:00:00+00:00  38575.039062  38575.039062   33286144  NaN  NaN   

                           50_EMA  Trend_Direction  Uptrend_Continuation  \
Datetime                                                                   
2022-02-01 00:00:00+00:00     NaN                0                 False   
2022-02-01 01:00:00+00:00     NaN                0                 False   
2022-02-01 02:00:00+00:00     NaN                0                 False   
2022-02-01 03:00:00+00:00     NaN                0                 False   
2022-02-01 04:00:00+00:00     NaN                0                 False   

                           Downtrend_Continuation  Buy_Signal  Sell_Signal  
Datetime                                                                    
2022-02-01 00:00:00+00:00                   False       False        False  
2022-02-01 01:00:00+00:00                   False       False        False  
2022-02-01 02:00:00+00:00                   False       False        False  
2022-02-01 03:00:00+00:00                   False       False        False  
2022-02-01 04:00:00+00:00                   False       False        False

In [31]:
#Create full entry conditions
enter_long = (data['Uptrend_Continuation'] & (data['ADX'] > 25) & (data['RSI'] > 70) & (data['Buy_Signal']))
enter_short = (data['Downtrend_Continuation'] & (data['ADX'] > 25) & (data['RSI'] < 30) & (data['Sell_Signal']))

In [32]:
#Create Exits
exit_long = (data['ADX'] < 25)
exit_short = (data['ADX'] < 25)

4. **Backtest**

In [34]:
#Backtest Strategy
#Create empty dataframe
signals_df = pd.DataFrame({
    'entries': 0,
    'exits': 0,
}, index=data.index)

#Set entry signals
signals_df['entries'][np.array(enter_long)] = 1
signals_df['entries'][np.array(enter_short)] = -1

#Set exit signals
signals_df['exits'][np.array(exit_long)] = 1
signals_df['exits'][np.array(exit_short)] = -1

#Run backtest using VectorBT
portfolio = vbt.Portfolio.from_signals(
    close=data['Close'],
    entries=signals_df['entries'],
    exits=signals_df['exits']
)

portfolio.plot().show() #Plot results
print(portfolio.stats()) #View strategy stats

/usr/local/lib/python3.10/dist-packages/vectorbt/generic/stats_builder.py:396: UserWarning:

Metric 'sharpe_ratio' requires frequency to be set

/usr/local/lib/python3.10/dist-packages/vectorbt/generic/stats_builder.py:396: UserWarning:

Metric 'calmar_ratio' requires frequency to be set

/usr/local/lib/python3.10/dist-packages/vectorbt/generic/stats_builder.py:396: UserWarning:

Metric 'omega_ratio' requires frequency to be set

/usr/local/lib/python3.10/dist-packages/vectorbt/generic/stats_builder.py:396: UserWarning:

Metric 'sortino_ratio' requires frequency to be set



Start                         2022-02-01 00:00:00+00:00
End                           2023-12-31 23:00:00+00:00
Period                                            16754
Start Value                                       100.0
End Value                                    117.899259
Total Return [%]                              17.899259
Benchmark Return [%]                          10.207597
Max Gross Exposure [%]                            100.0
Total Fees Paid                                     0.0
Max Drawdown [%]                              51.877618
Max Drawdown Duration                           15767.0
Total Trades                                        132
Total Closed Trades                                 132
Total Open Trades                                     0
Open Trade PnL                                      0.0
Win Rate [%]                                  56.818182
Best Trade [%]                                18.792021
Worst Trade [%]                              -25